In [5]:
import pandas as pd
import numpy as np
import xml.etree.ElementTree as et
from io import StringIO
import re
import os

data_path = []
data_names = []

#1. Import the xml file and parse it through element tree
#while visiting each folder, enter the folder again. If the file is xml, extract the path
def search(dir):
    data_paths = []
    data_names = []
    files = os.listdir(dir)
    for file_ in files:
        data_names.append(file_)
        filename = os.path.join(dir,file_)
        data_paths.append(filename)
    return data_paths, data_names

data_path, data_names = search('./articles')

In [6]:
file_paths = []
file_names = []

def file_folder_split(dir):
    for x in os.listdir(dir):
        if os.path.isfile(os.path.join(dir, x)) and "xml" in x:
            file_paths.append(os.path.join(dir, x))
            file_names.append(x)
            #print("File ==> {0}".format(x))
        if os.path.isdir(os.path.join(dir, x)):
            new_dir = os.path.join(dir, x)
            new_dir = new_dir.replace("./articles", "./result")
            if not(os.path.isdir(new_dir)):
                os.makedirs(new_dir)
            #print("Folder ==> {0}".format(x))
            file_folder_split(os.path.join(dir, x))

file_folder_split('./articles') 
print(len(file_paths))

21961


In [15]:
def remove_namespace(doc, namespace):
    #Remove namespace in the passed document in place.
    ns = u'{%s}' % namespace
    nsl = len(ns)
    for elem in doc.getiterator():
        if elem.tag.startswith(ns):
            elem.tag = elem.tag[nsl:]

def printResult(regex, repl, text):
    value = re.sub(regex, repl, text)
    #print ('# -- '+ regex, '\n', value, '\n', '-' * 30)
    return value

def stripWipsTag(text):
    text = printResult("<(/)?hlt[^>]*>", "", text)  # <hlt~></hlt~> 태그 제거
    return text

def extract_xml(root):
    test = []
    test_paragraph = []
    date = []
    for tags in root.iter("ppsarticleResultSet"):
        for articles in tags.iter("ppsarticle"):
            tmp = ""
            tmp_no = ""
            tmp_date = ""
            for no in articles.iter("accessionNo"):
                tmp_no = no.text
            for lParagraph in articles.iter("leadParagraph"):
                for paragraph in lParagraph.iter("paragraph"):
                    tmp += paragraph.text
            for tail in articles.iter("tailParagraphs"):
                for tail_paragraph in tail.iter("paragraph"):
                    tmp += tail_paragraph.text
            for dateTime in articles.iter("publicationDate"):
                for fulldate in dateTime.iter("dateTime"):
                    tmp_date += fulldate.text
            if tmp == "" or tmp_no == "" or tmp_date == "":
                continue
                #test_paragraph.append("None")
            test.append(tmp_no)
            test_paragraph.append(tmp)
            date.append(tmp_date)
    return test, test_paragraph, date

In [41]:
articles_df = []
data_index = 0
for data in file_names:
    #print(data)
    data = data.replace("articles_", "")
    data = data.replace(".xml.xml", ".xml")
    data = data.split('_')

    if len(data) == 4:
        company = data[0] + " " + data[1]
        gvkey = data[2]
        index, temp = data[3].split('.')
    elif len(data) == 3:
        company = data[0]
        gvkey = data[1]
        index, temp = data[2].split('.')
    elif len(data) == 5:
        company = data[0]
        gvkey = data[1]
        index, temp = data[4].split('.')
    
    xml_data = file_paths[data_index]
    #print(xml_data)
    try:
        doc = et.parse(xml_data)
    except et.ParseError:
        #log error
        data_index += 1
        continue

    # This was the namespace that was contained. EX) PPSarticle -> http://global.factiva.com.ezlibproxy1.ntu.edu.sg/pps/2.0PPSarticle
    remove_namespace(doc, u'http://global.factiva.com.ezlibproxy1.ntu.edu.sg/pps/2.0')
    root = doc.getroot()

    #removing hlt tag
    s = et.tostring(root, encoding = 'unicode')
    s = stripWipsTag(s)
    root = et.fromstring(s)

    #extraction and transformation
    test, test_paragraph, test_date = extract_xml(root)
    print( str(len(test)) + " / " + str(len(test_paragraph)) + "/" + str(len(test_date)))
    data = {'company': company, 'gvkey': gvkey, 'accessNo': test, 'article' : test_paragraph, 'date': test_date}
    df = pd.DataFrame(data)
    articles_df.append(df)
    
    new_dir = xml_data.replace("./articles", "./result")
    print(new_dir)
    new_dir = new_dir.split(".")[1]
    print(new_dir)
    df.to_csv( "." + new_dir + '.csv', index = False)
    data_index += 1


97 / 97/97
./result\Quantify1\Company\Chong It\ABOUT COM INC_119214_1.xml
/result\Quantify1\Company\Chong It\ABOUT COM INC_119214_1
97 / 97/97
./result\Quantify1\Company\Chong It\ABOUT COM INC_119214_2.xml
/result\Quantify1\Company\Chong It\ABOUT COM INC_119214_2
64 / 64/64
./result\Quantify1\Company\Chong It\ABOUT COM INC_119214_3.xml
/result\Quantify1\Company\Chong It\ABOUT COM INC_119214_3
92 / 92/92
./result\Quantify1\Company\Chong It\ABR INFORMATION SERVICES INC_30248_1.xml
/result\Quantify1\Company\Chong It\ABR INFORMATION SERVICES INC_30248_1
96 / 96/96
./result\Quantify1\Company\Chong It\ABR INFORMATION SERVICES INC_30248_2.xml
/result\Quantify1\Company\Chong It\ABR INFORMATION SERVICES INC_30248_2
96 / 96/96
./result\Quantify1\Company\Chong It\ABR INFORMATION SERVICES INC_30248_3.xml
/result\Quantify1\Company\Chong It\ABR INFORMATION SERVICES INC_30248_3
22 / 22/22
./result\Quantify1\Company\Chong It\ABR INFORMATION SERVICES INC_30248_4.xml
/result\Quantify1\Company\Chong It\A

0 / 0/0
./result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_1.xml
/result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_1
73 / 73/73
./result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_10.xml
/result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_10
74 / 74/74
./result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_11.xml
/result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_11
78 / 78/78
./result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_12.xml
/result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_12
81 / 81/81
./result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_13.xml
/result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_13
73 / 73/73
./result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_14.xml
/result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_14
83 / 83/83
./result\Quantify1\Company\Chong It\CONTINENTAL AIRLINES INC_10484_15.

93 / 93/93
./result\Quantify1\Company\Chong It\DADE BEHRING HOLDINGS INC_151016_2.xml
/result\Quantify1\Company\Chong It\DADE BEHRING HOLDINGS INC_151016_2
37 / 37/37
./result\Quantify1\Company\Chong It\DADE BEHRING HOLDINGS INC_151016_3.xml
/result\Quantify1\Company\Chong It\DADE BEHRING HOLDINGS INC_151016_3
90 / 90/90
./result\Quantify1\Company\Chong It\DEPOTECH CORP_61366_1.xml
/result\Quantify1\Company\Chong It\DEPOTECH CORP_61366_1
94 / 94/94
./result\Quantify1\Company\Chong It\DEPOTECH CORP_61366_2.xml
/result\Quantify1\Company\Chong It\DEPOTECH CORP_61366_2
30 / 30/30
./result\Quantify1\Company\Chong It\DEPOTECH CORP_61366_3.xml
/result\Quantify1\Company\Chong It\DEPOTECH CORP_61366_3
95 / 95/95
./result\Quantify1\Company\Chong It\DIATIDE INC_63040_1.xml
/result\Quantify1\Company\Chong It\DIATIDE INC_63040_1
92 / 92/92
./result\Quantify1\Company\Chong It\DIATIDE INC_63040_2.xml
/result\Quantify1\Company\Chong It\DIATIDE INC_63040_2
43 / 43/43
./result\Quantify1\Company\Chong It

95 / 95/95
./result\Quantify1\Company\Chong It\GEOWORKS CORP_30675_2.xml
/result\Quantify1\Company\Chong It\GEOWORKS CORP_30675_2
30 / 30/30
./result\Quantify1\Company\Chong It\GEOWORKS CORP_30675_3.xml
/result\Quantify1\Company\Chong It\GEOWORKS CORP_30675_3
91 / 91/91
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_1.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_1
97 / 97/97
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_10.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_10
92 / 92/92
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_11.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_11
94 / 94/94
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_12.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_12
92 / 92/92
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_13.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_13
84 / 84/84
./result\Quantify1\Co

86 / 86/86
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_60.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_60
85 / 85/85
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_61.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_61
79 / 79/79
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_62.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_62
87 / 87/87
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_63.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_63
88 / 88/88
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_64.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_64
80 / 80/80
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_65.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_65
91 / 91/91
./result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_66.xml
/result\Quantify1\Company\Chong It\GLAXOSMITHKLINE PLC_5180_66
85 / 8

...

94 / 94/94
./result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_73.xml
/result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_73
91 / 91/91
./result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_74.xml
/result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_74
89 / 89/89
./result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_75.xml
/result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_75
89 / 89/89
./result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_76.xml
/result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_76
93 / 93/93
./result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_77.xml
/result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_77
94 / 94/94
./result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_78.xml
/result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_78
80 / 80/80
./result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_79.xml
/result\Quantify9\Company\Chongit\GLAXOSMITHKLINE PLC_5180_79
90 / 90/90
./result\

80 / 80/80
./result\Quantify9\Company\Chongit\MARKETAXESS HOLDINGS INC_158742_2.xml
/result\Quantify9\Company\Chongit\MARKETAXESS HOLDINGS INC_158742_2
62 / 62/62
./result\Quantify9\Company\Chongit\MARKETAXESS HOLDINGS INC_158742_3.xml
/result\Quantify9\Company\Chongit\MARKETAXESS HOLDINGS INC_158742_3
95 / 95/95
./result\Quantify9\Company\Chongit\MMC NETWORKS INC_65705_1.xml
/result\Quantify9\Company\Chongit\MMC NETWORKS INC_65705_1
98 / 98/98
./result\Quantify9\Company\Chongit\MMC NETWORKS INC_65705_2.xml
/result\Quantify9\Company\Chongit\MMC NETWORKS INC_65705_2
94 / 94/94
./result\Quantify9\Company\Chongit\MMC NETWORKS INC_65705_3.xml
/result\Quantify9\Company\Chongit\MMC NETWORKS INC_65705_3
15 / 15/15
./result\Quantify9\Company\Chongit\MMC NETWORKS INC_65705_4.xml
/result\Quantify9\Company\Chongit\MMC NETWORKS INC_65705_4
99 / 99/99
./result\Quantify9\Company\Chongit\NET BANK INC_65170_1.xml
/result\Quantify9\Company\Chongit\NET BANK INC_65170_1
90 / 90/90
./result\Quantify9\Comp

15 / 15/15
./result\Quantify9\Company\Chongit\PIXAR_61627_40.xml
/result\Quantify9\Company\Chongit\PIXAR_61627_40
29 / 29/29
./result\Quantify9\Company\Chongit\PIXAR_61627_41.xml
/result\Quantify9\Company\Chongit\PIXAR_61627_41
33 / 33/33
./result\Quantify9\Company\Chongit\PIXAR_61627_42.xml
/result\Quantify9\Company\Chongit\PIXAR_61627_42
40 / 40/40
./result\Quantify9\Company\Chongit\PIXAR_61627_43.xml
/result\Quantify9\Company\Chongit\PIXAR_61627_43
30 / 30/30
./result\Quantify9\Company\Chongit\PIXAR_61627_44.xml
/result\Quantify9\Company\Chongit\PIXAR_61627_44
22 / 22/22
./result\Quantify9\Company\Chongit\PIXAR_61627_45.xml
/result\Quantify9\Company\Chongit\PIXAR_61627_45
28 / 28/28
./result\Quantify9\Company\Chongit\PIXAR_61627_46.xml
/result\Quantify9\Company\Chongit\PIXAR_61627_46
27 / 27/27
./result\Quantify9\Company\Chongit\PIXAR_61627_47.xml
/result\Quantify9\Company\Chongit\PIXAR_61627_47
29 / 29/29
./result\Quantify9\Company\Chongit\PIXAR_61627_48.xml
/result\Quantify9\Compa

0 / 0/0
./result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_3.xml
/result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_3
66 / 66/66
./result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_30.xml
/result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_30
79 / 79/79
./result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_31.xml
/result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_31
42 / 42/42
./result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_32.xml
/result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_32
2 / 2/2
./result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_4.xml
/result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_4
12 / 12/12
./result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_5.xml
/result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_5
43 / 43/43
./result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_6.xml
/result\Quantify9\Company\Chongit\SMITH & NEPHEW PLC_101317_6
88 / 88/88
./result\

77 / 77/77
./result\Quantify9\Company\Chongit\TEVA PHARMACEUTICAL INDUSTRIES LTD_14538_33.xml
/result\Quantify9\Company\Chongit\TEVA PHARMACEUTICAL INDUSTRIES LTD_14538_33
78 / 78/78
./result\Quantify9\Company\Chongit\TEVA PHARMACEUTICAL INDUSTRIES LTD_14538_34.xml
/result\Quantify9\Company\Chongit\TEVA PHARMACEUTICAL INDUSTRIES LTD_14538_34
72 / 72/72
./result\Quantify9\Company\Chongit\TEVA PHARMACEUTICAL INDUSTRIES LTD_14538_35.xml
/result\Quantify9\Company\Chongit\TEVA PHARMACEUTICAL INDUSTRIES LTD_14538_35
32 / 32/32
./result\Quantify9\Company\Chongit\TEVA PHARMACEUTICAL INDUSTRIES LTD_14538_36.xml
/result\Quantify9\Company\Chongit\TEVA PHARMACEUTICAL INDUSTRIES LTD_14538_36
55 / 55/55
./result\Quantify9\Company\Chongit\TEVA PHARMACEUTICAL INDUSTRIES LTD_14538_4.xml
/result\Quantify9\Company\Chongit\TEVA PHARMACEUTICAL INDUSTRIES LTD_14538_4
65 / 65/65
./result\Quantify9\Company\Chongit\TEVA PHARMACEUTICAL INDUSTRIES LTD_14538_5.xml
/result\Quantify9\Company\Chongit\TEVA PHARMACEUT

In [42]:
extracted_path = []
extracted_name = []

def file_folder_split_csv(dir):
    for x in os.listdir(dir):
        if os.path.isfile(os.path.join(dir, x)) and "csv" in x:
            extracted_path.append(os.path.join(dir, x))
            extracted_name.append(x)
        if os.path.isdir(os.path.join(dir, x)):
            new_dir = os.path.join(dir, x)
            file_folder_split_csv(os.path.join(dir, x))

file_folder_split_csv('./result') 

In [37]:
for i in range(1951, 2016):
    if not(os.path.isdir('./articles_english_with_date\\' + str(i))):
        os.makedirs('./articles_english_with_date\\' + str(i))

In [43]:
#4. Divide each file by year

data_index = 0
total_index = 0
for data in extracted_path:
    articles = pd.read_csv(data)
    #articles = articles[['ART_ID', 'ART_CONTENT', 'ART_DATE']].dropna(axis = 0)
    #articles = articles.reset_index()
    
    articles['date'] = articles['date'].str.replace('T', ' ')
    articles['date'] = articles['date'].str.replace('Z', '')
    articles['date'] = pd.to_datetime(articles['date'], format='%Y/%m/%d %H:%M:%S', utc=True)
    articles['year'] = pd.DatetimeIndex(articles['date']).year
    articles['month'] = pd.DatetimeIndex(articles['date']).month

    yearly_data = [None for i in range(65)]
    for i in range(1951, 2016):
        df = articles[articles['year'] == (i)]
        if(df.empty):
            yearly_data[(i-1951)] = None
        else:
            yearly_data[(i-1951)] = df
    
    for i in range(1951, 2016):
        if yearly_data[(i-1951)] is None:
            total_index += 1
            continue
        else:
            yearly_data[(i-1951)].to_csv('./articles_english_with_date\\'+ str(i) + '\\'+ str(total_index) + '.csv', index = False)
            total_index += 1
    data_index += 1

In [44]:
year_path = []
year_name = []

def file_folder_split_csv(dir):
    for x in os.listdir(dir):
        if os.path.isfile(os.path.join(dir, x)) and "csv" in x:
            year_path.append(os.path.join(dir, x))
            year_name.append(x)
        if os.path.isdir(os.path.join(dir, x)):
            new_dir = os.path.join(dir, x)
            file_folder_split_csv(os.path.join(dir, x))

file_folder_split_csv('./articles_english_with_date') 

In [52]:
print(year_path[0])

./articles_english_with_date\1991\215580.csv


In [45]:
def folder_copy(dir):
    for x in os.listdir(dir):
        if os.path.isdir(os.path.join(dir, x)):
            new_dir = os.path.join(dir, x)
            new_dir = new_dir.replace("./articles_english_with_date", "./articles_english_year_month")
            if not(os.path.isdir(new_dir)):
                os.makedirs(new_dir)
            folder_copy(os.path.join(dir, x))

folder_copy('./articles_english_with_date') 

In [49]:
for folders in os.listdir('./articles_english_year_month'):
    for i in range(1, 13):
        if not(os.path.isdir(os.path.join('./articles_english_year_month', folders) + '\\' + str(i))):
            os.makedirs(os.path.join('./articles_english_year_month', folders) + '\\' + str(i))

In [56]:
#4. Divide each file by month

data_index = 0
total_index = 0
for data in year_path:
    print(data)
    year = data.split('\\')[1]
    articles = pd.read_csv(data)

    monthly_data = [None for i in range(12)]
    for i in range(0, 12):
        df = articles[articles['month'] == (i+1)]
        if(df.empty):
            monthly_data[i] = None
        else:
            monthly_data[i] = df
    
    for i in range(0, 12):
        if monthly_data[i] is None:
            total_index += 1
            continue
        else:
            monthly_data[i].to_csv('./articles_english_year_month\\' + str(year) + '\\'+ str(i+1) + '\\' + str(total_index) + '.csv', index = False)
            total_index += 1
    data_index += 1

./articles_english_with_date\1991\215580.csv
./articles_english_with_date\1991\34425.csv
./articles_english_with_date\1991\374310.csv
./articles_english_with_date\1991\375025.csv
./articles_english_with_date\1991\375740.csv
./articles_english_with_date\1991\376455.csv
./articles_english_with_date\1991\403560.csv
./articles_english_with_date\1991\404990.csv
./articles_english_with_date\1991\421240.csv
./articles_english_with_date\1991\519065.csv
./articles_english_with_date\1991\519195.csv
./articles_english_with_date\1991\519715.csv
./articles_english_with_date\1991\680265.csv
./articles_english_with_date\1991\680330.csv
./articles_english_with_date\1991\680395.csv
./articles_english_with_date\1991\680655.csv
./articles_english_with_date\1991\680720.csv
./articles_english_with_date\1991\680850.csv
./articles_english_with_date\1991\680915.csv
./articles_english_with_date\1991\681045.csv
./articles_english_with_date\1992\150971.csv
./articles_english_with_date\1992\215581.csv
./articles_

./articles_english_with_date\1994\653163.csv
./articles_english_with_date\1994\6608.csv
./articles_english_with_date\1994\678903.csv
./articles_english_with_date\1994\678968.csv
./articles_english_with_date\1994\679423.csv
./articles_english_with_date\1994\679488.csv
./articles_english_with_date\1994\679813.csv
./articles_english_with_date\1994\679878.csv
./articles_english_with_date\1994\683583.csv
./articles_english_with_date\1994\683648.csv
./articles_english_with_date\1994\683713.csv
./articles_english_with_date\1994\683778.csv
./articles_english_with_date\1994\683843.csv
./articles_english_with_date\1994\683908.csv
./articles_english_with_date\1994\683973.csv
./articles_english_with_date\1994\684103.csv
./articles_english_with_date\1994\717838.csv
./articles_english_with_date\1994\718098.csv
./articles_english_with_date\1994\719138.csv
./articles_english_with_date\1994\719658.csv
./articles_english_with_date\1994\720178.csv
./articles_english_with_date\1994\720503.csv
./articles_e

./articles_english_with_date\1995\34754.csv
./articles_english_with_date\1995\3554.csv
./articles_english_with_date\1995\368334.csv
./articles_english_with_date\1995\369049.csv
./articles_english_with_date\1995\37224.csv
./articles_english_with_date\1995\37289.csv
./articles_english_with_date\1995\374834.csv
./articles_english_with_date\1995\374899.csv
./articles_english_with_date\1995\374964.csv
./articles_english_with_date\1995\375094.csv
./articles_english_with_date\1995\383934.csv
./articles_english_with_date\1995\383999.csv
./articles_english_with_date\1995\384064.csv
./articles_english_with_date\1995\384194.csv
./articles_english_with_date\1995\394269.csv
./articles_english_with_date\1995\399209.csv
./articles_english_with_date\1995\399924.csv
./articles_english_with_date\1995\403629.csv
./articles_english_with_date\1995\403694.csv
./articles_english_with_date\1995\411559.csv
./articles_english_with_date\1995\411624.csv
./articles_english_with_date\1995\420009.csv
./articles_engl

./articles_english_with_date\1995\727329.csv
./articles_english_with_date\1995\727654.csv
./articles_english_with_date\1995\729279.csv
./articles_english_with_date\1995\729409.csv
./articles_english_with_date\1995\730124.csv
./articles_english_with_date\1995\732464.csv
./articles_english_with_date\1995\733049.csv
./articles_english_with_date\1995\733439.csv
./articles_english_with_date\1995\736494.csv
./articles_english_with_date\1995\736624.csv
./articles_english_with_date\1995\736689.csv
./articles_english_with_date\1995\737014.csv
./articles_english_with_date\1995\737534.csv
./articles_english_with_date\1995\741239.csv
./articles_english_with_date\1995\748064.csv
./articles_english_with_date\1995\749104.csv
./articles_english_with_date\1995\749559.csv
./articles_english_with_date\1995\750144.csv
./articles_english_with_date\1995\752029.csv
./articles_english_with_date\1995\756059.csv
./articles_english_with_date\1995\756189.csv
./articles_english_with_date\1995\756384.csv
./articles

./articles_english_with_date\1996\342985.csv
./articles_english_with_date\1996\34755.csv
./articles_english_with_date\1996\34885.csv
./articles_english_with_date\1996\3555.csv
./articles_english_with_date\1996\369050.csv
./articles_english_with_date\1996\369765.csv
./articles_english_with_date\1996\37355.csv
./articles_english_with_date\1996\37420.csv
./articles_english_with_date\1996\375095.csv
./articles_english_with_date\1996\375160.csv
./articles_english_with_date\1996\375225.csv
./articles_english_with_date\1996\375290.csv
./articles_english_with_date\1996\3815.csv
./articles_english_with_date\1996\384195.csv
./articles_english_with_date\1996\384260.csv
./articles_english_with_date\1996\384325.csv
./articles_english_with_date\1996\384390.csv
./articles_english_with_date\1996\394335.csv
./articles_english_with_date\1996\394400.csv
./articles_english_with_date\1996\394465.csv
./articles_english_with_date\1996\394530.csv
./articles_english_with_date\1996\403695.csv
./articles_english

...

./articles_english_with_date\2009\465653.csv
./articles_english_with_date\2009\465718.csv
./articles_english_with_date\2009\465783.csv
./articles_english_with_date\2009\465848.csv
./articles_english_with_date\2009\465913.csv
./articles_english_with_date\2009\465978.csv
./articles_english_with_date\2009\466043.csv
./articles_english_with_date\2009\466108.csv
./articles_english_with_date\2009\466173.csv
./articles_english_with_date\2009\466238.csv
./articles_english_with_date\2009\466303.csv
./articles_english_with_date\2009\466368.csv
./articles_english_with_date\2009\466433.csv
./articles_english_with_date\2009\466498.csv
./articles_english_with_date\2009\466563.csv
./articles_english_with_date\2009\466628.csv
./articles_english_with_date\2009\466693.csv
./articles_english_with_date\2009\466758.csv
./articles_english_with_date\2009\466823.csv
./articles_english_with_date\2009\466888.csv
./articles_english_with_date\2009\466953.csv
./articles_english_with_date\2009\467018.csv
./articles

./articles_english_with_date\2009\508618.csv
./articles_english_with_date\2009\508683.csv
./articles_english_with_date\2009\508748.csv
./articles_english_with_date\2009\508813.csv
./articles_english_with_date\2009\508878.csv
./articles_english_with_date\2009\508943.csv
./articles_english_with_date\2009\509008.csv
./articles_english_with_date\2009\509073.csv
./articles_english_with_date\2009\509138.csv
./articles_english_with_date\2009\509203.csv
./articles_english_with_date\2009\509268.csv
./articles_english_with_date\2009\509333.csv
./articles_english_with_date\2009\509398.csv
./articles_english_with_date\2009\509463.csv
./articles_english_with_date\2009\509528.csv
./articles_english_with_date\2009\509593.csv
./articles_english_with_date\2009\509658.csv
./articles_english_with_date\2009\509723.csv
./articles_english_with_date\2009\509788.csv
./articles_english_with_date\2009\509853.csv
./articles_english_with_date\2009\509918.csv
./articles_english_with_date\2009\509983.csv
./articles

./articles_english_with_date\2009\577388.csv
./articles_english_with_date\2009\577453.csv
./articles_english_with_date\2009\577518.csv
./articles_english_with_date\2009\577583.csv
./articles_english_with_date\2009\577648.csv
./articles_english_with_date\2009\577713.csv
./articles_english_with_date\2009\577778.csv
./articles_english_with_date\2009\577908.csv
./articles_english_with_date\2009\577973.csv
./articles_english_with_date\2009\578038.csv
./articles_english_with_date\2009\578103.csv
./articles_english_with_date\2009\578623.csv
./articles_english_with_date\2009\578688.csv
./articles_english_with_date\2009\578753.csv
./articles_english_with_date\2009\578818.csv
./articles_english_with_date\2009\579078.csv
./articles_english_with_date\2009\579273.csv
./articles_english_with_date\2009\579338.csv
./articles_english_with_date\2009\579468.csv
./articles_english_with_date\2009\579663.csv
./articles_english_with_date\2009\579793.csv
./articles_english_with_date\2009\579858.csv
./articles

./articles_english_with_date\2009\628023.csv
./articles_english_with_date\2009\628088.csv
./articles_english_with_date\2009\628153.csv
./articles_english_with_date\2009\628218.csv
./articles_english_with_date\2009\628283.csv
./articles_english_with_date\2009\628348.csv
./articles_english_with_date\2009\628413.csv
./articles_english_with_date\2009\628478.csv
./articles_english_with_date\2009\628543.csv
./articles_english_with_date\2009\628608.csv
./articles_english_with_date\2009\628673.csv
./articles_english_with_date\2009\628738.csv
./articles_english_with_date\2009\628803.csv
./articles_english_with_date\2009\628868.csv
./articles_english_with_date\2009\628933.csv
./articles_english_with_date\2009\628998.csv
./articles_english_with_date\2009\629063.csv
./articles_english_with_date\2009\629128.csv
./articles_english_with_date\2009\62913.csv
./articles_english_with_date\2009\629193.csv
./articles_english_with_date\2009\629258.csv
./articles_english_with_date\2009\629323.csv
./articles_

./articles_english_with_date\2009\716423.csv
./articles_english_with_date\2009\716488.csv
./articles_english_with_date\2009\716553.csv
./articles_english_with_date\2009\716618.csv
./articles_english_with_date\2009\716683.csv
./articles_english_with_date\2009\716748.csv
./articles_english_with_date\2009\716813.csv
./articles_english_with_date\2009\716878.csv
./articles_english_with_date\2009\716943.csv
./articles_english_with_date\2009\717008.csv
./articles_english_with_date\2009\717073.csv
./articles_english_with_date\2009\717138.csv
./articles_english_with_date\2009\717203.csv
./articles_english_with_date\2009\717268.csv
./articles_english_with_date\2009\717333.csv
./articles_english_with_date\2009\717398.csv
./articles_english_with_date\2009\717463.csv
./articles_english_with_date\2009\717528.csv
./articles_english_with_date\2009\719543.csv
./articles_english_with_date\2009\719608.csv
./articles_english_with_date\2009\722793.csv
./articles_english_with_date\2009\724483.csv
./articles